In [124]:
# import the relevant libraries

import numpy as np
import pandas as pd
import seaborn as sns
import os
import matplotlib.pyplot as plt
import seaborn as sns

#regression
from sklearn.linear_model import LinearRegression,Ridge,Lasso,RidgeCV
from sklearn.ensemble import RandomForestRegressor,BaggingRegressor,GradientBoostingRegressor,AdaBoostRegressor
from sklearn.svm import SVR
from sklearn.neighbors import KNeighborsRegressor

#model selection
from sklearn.model_selection import train_test_split,cross_validate
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV

#evaluation metrics
from sklearn.metrics import mean_squared_log_error,mean_squared_error, r2_score,mean_absolute_error # for regression

In [125]:
file_path = ('/Users/juandavidbotero/Desktop/2ndDataScience/')

#df_hour = pd.read_csv(os.path.join(file_path, 'train.csv'), parse_dates=['datetime'], index_col='datetime')


train_set = pd.read_csv(os.path.join(file_path, 'train.csv'))
test_set = pd.read_csv(os.path.join(file_path, 'test.csv'))
holiday = pd.read_csv(os.path.join(file_path, 'holidays.csv'))
df = train_set.copy()
test_df = test_set.copy()

### COMBINING

##### We combine the test and train sets so that all the features we create will be present in both datasets. 
##### In order to have the same dimentions, a label column on the test_set is created and the values are set to zero.

In [126]:
test_set['countRents'] = 0

dataset = pd.concat([train_set,test_set], axis = 0)

In [127]:
dataset.head()

datetime        summary                 icon  precipIntensity  \
0  2017-01-01 00:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
1  2017-01-01 01:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2  2017-01-01 02:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
3  2017-01-01 03:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
4  2017-01-01 04:00:00  Mostly Cloudy  partly-cloudy-night           0.0116   

   precipProbability  temperature  apparentTemperature  dewPoint  humidity  \
0                0.0         6.80                 6.11      5.66      0.92   
1                0.0         6.36                 5.28      5.27      0.93   
2                0.0         6.04                 5.12      4.80      0.92   
3                0.0         5.79                 5.79      4.61      0.92   
4                0.1         5.57                 4.74      4.41      0.92   

   windSpeed  windGust  windBearing  cloudCover  uvIndex  visibility  \
0       1.41      3.12        227.0        0.77      0.0       7.179   
1       1.69      3.16        218.0        0.77      0.0       5.863   
2       1.51      3.13        222.0        0.83      0.0       6.354   
3       1.33      2.94        214.0        0.71      0.0       5.935   
4       1.39      3.08        202.0        0.83      0.0       5.981   

  precipType  pressure  precipAccumulation  ozone  countRents  
0        NaN       NaN                 NaN    NaN         932  
1        NaN       NaN                 NaN    NaN         892  
2        NaN       NaN                 NaN    NaN         339  
3        NaN       NaN                 NaN    NaN         282  
4       rain       NaN                 NaN    NaN         185

In [128]:
dataset['countRents'].describe()

count    23232.000000
mean      1151.952996
std       1146.402109
min          0.000000
25%        189.000000
50%        841.000000
75%       1712.000000
max       6423.000000
Name: countRents, dtype: float64

In [129]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23232 entries, 0 to 743
Data columns (total 20 columns):
datetime               23232 non-null object
summary                23206 non-null object
icon                   23206 non-null object
precipIntensity        19507 non-null float64
precipProbability      19507 non-null float64
temperature            23201 non-null float64
apparentTemperature    23201 non-null float64
dewPoint               23205 non-null float64
humidity               23201 non-null float64
windSpeed              23188 non-null float64
windGust               20093 non-null float64
windBearing            23177 non-null float64
cloudCover             22196 non-null float64
uvIndex                22666 non-null float64
visibility             23177 non-null float64
precipType             8747 non-null object
pressure               19466 non-null float64
precipAccumulation     48 non-null float64
ozone                  7403 non-null float64
countRents             23232

In [130]:
dataset.isnull().sum()  # find missing values

datetime                   0
summary                   26
icon                      26
precipIntensity         3725
precipProbability       3725
temperature               31
apparentTemperature       31
dewPoint                  27
humidity                  31
windSpeed                 44
windGust                3139
windBearing               55
cloudCover              1036
uvIndex                  566
visibility                55
precipType             14485
pressure                3766
precipAccumulation     23184
ozone                  15829
countRents                 0
dtype: int64

In [131]:
dataset.describe() # describe the numerical columns

precipIntensity  precipProbability   temperature  apparentTemperature  \
count     19507.000000       19507.000000  23201.000000         23201.000000   
mean          0.048498           0.070425     12.184749            11.610307   
std           0.188912           0.175120      6.392663             7.049909   
min           0.000000           0.000000     -5.740000            -9.280000   
25%           0.000000           0.000000      7.580000             6.200000   
50%           0.000000           0.000000     11.750000            11.750000   
75%           0.005900           0.010000     16.670000            16.690000   
max           6.214500           0.980000     36.630000            37.540000   

           dewPoint      humidity     windSpeed      windGust   windBearing  \
count  23205.000000  23201.000000  23188.000000  20093.000000  23177.000000   
mean       7.602211      0.757439      2.757878      5.088107    198.139017   
std        4.958802      0.154688      1.772683      3.713379     92.394195   
min       -8.630000      0.230000      0.000000      0.000000      0.000000   
25%        4.060000      0.660000      1.510000      2.330000    129.000000   
50%        7.930000      0.800000      2.470000      4.200000    220.000000   
75%       11.430000      0.880000      3.672500      7.130000    263.000000   
max       19.140000      1.000000     13.590000     21.160000    359.000000   

         cloudCover       uvIndex    visibility      pressure  \
count  22196.000000  22666.000000  23177.000000  19466.000000   
mean       0.557456      0.904968      9.314413   1015.435408   
std        0.330272      1.611196      2.029269     10.889521   
min        0.000000      0.000000      0.000000    971.750000   
25%        0.250000      0.000000      9.795000   1008.950000   
50%        0.640000      0.000000     10.003000   1016.270000   
75%        0.840000      1.000000     10.003000   1022.820000   
max        1.000000      9.000000     16.093000   1044.180000   

       precipAccumulation        ozone    countRents  
count           48.000000  7403.000000  23232.000000  
mean             0.152571   335.418803   1151.952996  
std              0.194139    42.380998   1146.402109  
min              0.005400   239.200000      0.000000  
25%              0.014100   305.500000    189.000000  
50%              0.051700   332.600000    841.000000  
75%              0.194200   359.100000   1712.000000  
max              0.606400   485.400000   6423.000000

In [132]:
holiday.head()

date holiday
0  2019-01-01       Y
1  2019-04-19       Y
2  2019-04-22       Y
3  2019-05-06       Y
4  2019-05-27       Y

In [42]:
import pandas_profiling 

In [43]:
pandas_profiling.ProfileReport(dataset)

# DROP IRRELEVANT VARIABLES

In [133]:
dataset = dataset.drop('precipAccumulation', axis = 1)
dataset = dataset.drop('temperature', axis = 1)
dataset = dataset.drop('windGust', axis = 1)

# Missing values (NA's)

In [134]:
dataset['cloudCover'] = dataset['cloudCover'].fillna(value=(dataset['cloudCover'].mean()))
dataset['ozone'] = dataset['ozone'].fillna(value=0)
dataset['precipProbability'] = dataset['precipProbability'].fillna(value=(dataset['precipProbability'].mode()))
dataset['precipType'] = dataset['precipType'].fillna(value='none')
dataset['pressure'] = dataset['pressure'].fillna(value=(dataset['pressure'].median()))
dataset['uvIndex'] = dataset['uvIndex'].fillna(value=(dataset['uvIndex'].mean()))
dataset['apparentTemperature'] = dataset['apparentTemperature'].fillna(value=(dataset['apparentTemperature'].median()))
dataset['dewPoint'] = dataset['dewPoint'].fillna(value=(dataset['dewPoint'].median()))
dataset['humidity'] = dataset['humidity'].fillna(value=(dataset['humidity'].median()))
dataset['icon'] = dataset['icon'].fillna(value='partly-cloudy-day')
dataset['summary'] = dataset['summary'].fillna(value='Mostly Cloudy')
dataset['windBearing'] = dataset['windBearing'].fillna(value=(dataset['windBearing'].median()))
dataset['windSpeed'] = dataset['windSpeed'].fillna(value=(dataset['windSpeed'].median()))
dataset['visibility'] = dataset['visibility'].fillna(value=10.003)
dataset['precipProbability'] = dataset['precipProbability'].fillna(value=0.07042548829)
dataset['precipIntensity'] = dataset['precipIntensity'].fillna(value=0.04849824166)

In [46]:
pandas_profiling.ProfileReport(dataset)

In [135]:
dataset.isnull().sum()  # find missing values

datetime               0
summary                0
icon                   0
precipIntensity        0
precipProbability      0
apparentTemperature    0
dewPoint               0
humidity               0
windSpeed              0
windBearing            0
cloudCover             0
uvIndex                0
visibility             0
precipType             0
pressure               0
ozone                  0
countRents             0
dtype: int64

# Feature Creation

In [137]:
dataset["hour"] = [t.hour for t in pd.DatetimeIndex(dataset.datetime)]
dataset["day"] = [t.dayofweek for t in pd.DatetimeIndex(dataset.datetime)]
dataset["month"] = [t.month for t in pd.DatetimeIndex(dataset.datetime)]
dataset['year'] = [t.year for t in pd.DatetimeIndex(dataset.datetime)]
dataset['quarter'] = [t.quarter for t in pd.DatetimeIndex(dataset.datetime)]
dataset['year'] = dataset['year'].map({2017:0, 2018:1, 2019:2})
dataset.head()

datetime        summary                 icon  precipIntensity  \
0  2017-01-01 00:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
1  2017-01-01 01:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2  2017-01-01 02:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
3  2017-01-01 03:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
4  2017-01-01 04:00:00  Mostly Cloudy  partly-cloudy-night           0.0116   

   precipProbability  apparentTemperature  dewPoint  humidity  windSpeed  \
0                0.0                 6.11      5.66      0.92       1.41   
1                0.0                 5.28      5.27      0.93       1.69   
2                0.0                 5.12      4.80      0.92       1.51   
3                0.0                 5.79      4.61      0.92       1.33   
4                0.1                 4.74      4.41      0.92       1.39   

   windBearing  ...  visibility  precipType  pressure ozone  countRents  hour  \
0        227.0  ...       7.179        none   1016.27   0.0         932     0   
1        218.0  ...       5.863        none   1016.27   0.0         892     1   
2        222.0  ...       6.354        none   1016.27   0.0         339     2   
3        214.0  ...       5.935        none   1016.27   0.0         282     3   
4        202.0  ...       5.981        rain   1016.27   0.0         185     4   

   day  month  year  quarter  
0    6      1     0        1  
1    6      1     0        1  
2    6      1     0        1  
3    6      1     0        1  
4    6      1     0        1  

[5 rows x 22 columns]

In [143]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
Index: 23232 entries, 2017-01-01 00:00:00 to 2019-08-26 23:00:00
Data columns (total 24 columns):
summary                23232 non-null object
icon                   23232 non-null object
precipIntensity        23232 non-null float64
precipProbability      23232 non-null float64
apparentTemperature    23232 non-null float64
dewPoint               23232 non-null float64
humidity               23232 non-null float64
windSpeed              23232 non-null float64
windBearing            23232 non-null float64
cloudCover             23232 non-null float64
uvIndex                23232 non-null float64
visibility             23232 non-null float64
precipType             23232 non-null object
pressure               23232 non-null float64
ozone                  23232 non-null float64
countRents             23232 non-null int64
hour                   23232 non-null int64
day                    23232 non-null int64
month                  23232 non-null int64
y

In [141]:
dataset.set_index('datetime', inplace=True)

In [144]:
dataset['apt_humd'] = dataset['apparentTemperature'] * dataset['humidity']
dataset['hum_cloud'] = dataset['cloudCover'] + dataset['humidity']
dataset['windspeed_apptem'] = dataset['apparentTemperature'] * dataset['windSpeed']
dataset['season_tem'] = dataset['quarter'] * dataset['windspeed_apptem'] * dataset['apt_humd']

In [145]:
dataset.head()

summary                 icon  precipIntensity  \
datetime                                                                   
2017-01-01 00:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2017-01-01 01:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2017-01-01 02:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2017-01-01 03:00:00  Mostly Cloudy  partly-cloudy-night           0.0000   
2017-01-01 04:00:00  Mostly Cloudy  partly-cloudy-night           0.0116   

                     precipProbability  apparentTemperature  dewPoint  \
datetime                                                                
2017-01-01 00:00:00                0.0                 6.11      5.66   
2017-01-01 01:00:00                0.0                 5.28      5.27   
2017-01-01 02:00:00                0.0                 5.12      4.80   
2017-01-01 03:00:00                0.0                 5.79      4.61   
2017-01-01 04:00:00                0.1                 4.74      4.41   

                     humidity  windSpeed  windBearing  cloudCover  ...  \
datetime                                                           ...   
2017-01-01 00:00:00      0.92       1.41        227.0        0.77  ...   
2017-01-01 01:00:00      0.93       1.69        218.0        0.77  ...   
2017-01-01 02:00:00      0.92       1.51        222.0        0.83  ...   
2017-01-01 03:00:00      0.92       1.33        214.0        0.71  ...   
2017-01-01 04:00:00      0.92       1.39        202.0        0.83  ...   

                     countRents  hour day  month  year  quarter  apt_humd  \
datetime                                                                    
2017-01-01 00:00:00         932     0   6      1     0        1    5.6212   
2017-01-01 01:00:00         892     1   6      1     0        1    4.9104   
2017-01-01 02:00:00         339     2   6      1     0        1    4.7104   
2017-01-01 03:00:00         282     3   6      1     0        1    5.3268   
2017-01-01 04:00:00         185     4   6      1     0        1    4.3608   

                     hum_cloud  windspeed_apptem  season_tem  
datetime                                                      
2017-01-01 00:00:00       1.69            8.6151   48.427200  
2017-01-01 01:00:00       1.70            8.9232   43.816481  
2017-01-01 02:00:00       1.75            7.7312   36.417044  
2017-01-01 03:00:00       1.63            7.7007   41.020089  
2017-01-01 04:00:00       1.75            6.5886   28.731567  

[5 rows x 25 columns]

# Modeling

In [146]:
dummy_dataset = pd.get_dummies(dataset.drop('countRents', axis=1))

In [147]:
selected = pd.merge(dataset['countRents'],dummy_dataset, left_index=True, right_index=True)

In [148]:
np.random.seed(42)

train_set_final = selected.loc[:'2019-07-26',:]
test_set_final = selected.loc['2019-07-27':,:]

In [149]:
train_set_final.shape

(22464, 58)

In [150]:
test_set_final.shape

(744, 58)

In [151]:
test_set_final = test_set_final.drop('countRents', axis = 1)

In [152]:
train_set_final.head()

countRents  precipIntensity  precipProbability  \
datetime                                                              
2017-01-01 00:00:00         932           0.0000                0.0   
2017-01-01 01:00:00         892           0.0000                0.0   
2017-01-01 02:00:00         339           0.0000                0.0   
2017-01-01 03:00:00         282           0.0000                0.0   
2017-01-01 04:00:00         185           0.0116                0.1   

                     apparentTemperature  dewPoint  humidity  windSpeed  \
datetime                                                                  
2017-01-01 00:00:00                 6.11      5.66      0.92       1.41   
2017-01-01 01:00:00                 5.28      5.27      0.93       1.69   
2017-01-01 02:00:00                 5.12      4.80      0.92       1.51   
2017-01-01 03:00:00                 5.79      4.61      0.92       1.33   
2017-01-01 04:00:00                 4.74      4.41      0.92       1.39   

                     windBearing  cloudCover  uvIndex  ...  \
datetime                                               ...   
2017-01-01 00:00:00        227.0        0.77      0.0  ...   
2017-01-01 01:00:00        218.0        0.77      0.0  ...   
2017-01-01 02:00:00        222.0        0.83      0.0  ...   
2017-01-01 03:00:00        214.0        0.71      0.0  ...   
2017-01-01 04:00:00        202.0        0.83      0.0  ...   

                     icon_partly-cloudy-day  icon_partly-cloudy-night  \
datetime                                                                
2017-01-01 00:00:00                       0                         1   
2017-01-01 01:00:00                       0                         1   
2017-01-01 02:00:00                       0                         1   
2017-01-01 03:00:00                       0                         1   
2017-01-01 04:00:00                       0                         1   

                     icon_rain  icon_sleet  icon_snow  icon_wind  \
datetime                                                           
2017-01-01 00:00:00          0           0          0          0   
2017-01-01 01:00:00          0           0          0          0   
2017-01-01 02:00:00          0           0          0          0   
2017-01-01 03:00:00          0           0          0          0   
2017-01-01 04:00:00          0           0          0          0   

                     precipType_none  precipType_rain  precipType_sleet  \
datetime                                                                  
2017-01-01 00:00:00                1                0                 0   
2017-01-01 01:00:00                1                0                 0   
2017-01-01 02:00:00                1                0                 0   
2017-01-01 03:00:00                1                0                 0   
2017-01-01 04:00:00                0                1                 0   

                     precipType_snow  
datetime                              
2017-01-01 00:00:00                0  
2017-01-01 01:00:00                0  
2017-01-01 02:00:00                0  
2017-01-01 03:00:00                0  
2017-01-01 04:00:00                0  

[5 rows x 58 columns]

In [153]:
test_set_final.head()

precipIntensity  precipProbability  apparentTemperature  \
datetime                                                                       
2019-07-27 00:00:00           0.1727               0.31                20.47   
2019-07-27 01:00:00           0.2754               0.49                19.64   
2019-07-27 02:00:00           0.5042               0.62                18.57   
2019-07-27 03:00:00           0.7826               0.66                18.23   
2019-07-27 04:00:00           0.9662               0.69                17.87   

                     dewPoint  humidity  windSpeed  windBearing  cloudCover  \
datetime                                                                      
2019-07-27 00:00:00     17.45      0.84       4.03        276.0        0.69   
2019-07-27 01:00:00     16.52      0.83       4.16        251.0        0.44   
2019-07-27 02:00:00     16.17      0.87       3.81        341.0        0.75   
2019-07-27 03:00:00     15.73      0.86       3.03        268.0        0.64   
2019-07-27 04:00:00     16.04      0.90       2.93        274.0        0.74   

                     uvIndex  visibility  ...  icon_partly-cloudy-day  \
datetime                                  ...                           
2019-07-27 00:00:00      0.0      10.566  ...                       0   
2019-07-27 01:00:00      0.0      10.587  ...                       0   
2019-07-27 02:00:00      0.0       8.223  ...                       0   
2019-07-27 03:00:00      0.0       9.099  ...                       0   
2019-07-27 04:00:00      0.0       6.996  ...                       0   

                     icon_partly-cloudy-night  icon_rain  icon_sleet  \
datetime                                                               
2019-07-27 00:00:00                         1          0           0   
2019-07-27 01:00:00                         0          1           0   
2019-07-27 02:00:00                         0          1           0   
2019-07-27 03:00:00                         0          1           0   
2019-07-27 04:00:00                         0          1           0   

                     icon_snow  icon_wind  precipType_none  precipType_rain  \
datetime                                                                      
2019-07-27 00:00:00          0          0                0                1   
2019-07-27 01:00:00          0          0                0                1   
2019-07-27 02:00:00          0          0                0                1   
2019-07-27 03:00:00          0          0                0                1   
2019-07-27 04:00:00          0          0                0                1   

                     precipType_sleet  precipType_snow  
datetime                                                
2019-07-27 00:00:00                 0                0  
2019-07-27 01:00:00                 0                0  
2019-07-27 02:00:00                 0                0  
2019-07-27 03:00:00                 0                0  
2019-07-27 04:00:00                 0                0  

[5 rows x 57 columns]

In [154]:
from sklearn.model_selection import train_test_split

In [155]:
X = train_set_final.drop('countRents', axis=1).values
y = train_set_final['countRents'].values

In [156]:
X_train, X_test, y_train, y_test = train_test_split(X,y, test_size=0.2)

In [157]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import accuracy_score

In [158]:
# set the random forest

param_grid = {
    'n_estimators': [5, 100],
    'max_features': ['auto','sqrt', 'log2']
}

random_f = RandomForestRegressor()

final = RandomizedSearchCV(estimator=random_f,param_distributions = param_grid,cv=None)

In [159]:
final.fit(X,y)

RandomizedSearchCV(cv=None, error_score='raise-deprecating',
                   estimator=RandomForestRegressor(bootstrap=True,
                                                   criterion='mse',
                                                   max_depth=None,
                                                   max_features='auto',
                                                   max_leaf_nodes=None,
                                                   min_impurity_decrease=0.0,
                                                   min_impurity_split=None,
                                                   min_samples_leaf=1,
                                                   min_samples_split=2,
                                                   min_weight_fraction_leaf=0.0,
                                                   n_estimators='warn',
                                                   n_jobs=None, oob_score=False,
                                                   random_stat

In [160]:
final.best_params_

{'n_estimators': 100, 'max_features': 'auto'}

In [161]:
random_f = RandomForestRegressor(n_estimators=100, max_features='auto')

In [162]:
# fit the model on the train set

model = random_f.fit(X, y)

In [163]:
# predict the count in the test set


y_final_pred = model.predict(test_set_final)

In [164]:
# predict the classes and set the column and index as required by driven-data

df_predictions = pd.DataFrame(model.predict(test_set_final))
df_predictions.columns = ['countRents']
df_predictions.index = test_set_final.index
df_predictions.head()

countRents
datetime                       
2019-07-27 00:00:00      421.72
2019-07-27 01:00:00      266.87
2019-07-27 02:00:00      167.32
2019-07-27 03:00:00      107.04
2019-07-27 04:00:00       88.84

In [165]:
# write predictions to file

df_predictions.to_csv(os.path.join(file_path, 'predictions6.csv'))

# Conclusion

The best model was a RandomForestRegressor(n_estimators=100, max_features='auto') with a score of 0.26160 with the file predictions3.csv

# New models

In [166]:
models=[RandomForestRegressor(),AdaBoostRegressor(),BaggingRegressor(),SVR(),KNeighborsRegressor()]
model_names=['RandomForestRegressor','AdaBoostRegressor','BaggingRegressor','SVR','KNeighborsRegressor']
rmsle=[]
d={}
for model in range (len(models)):
    clf=models[model]
    clf.fit(X_train,y_train)
    test_pred=clf.predict(X_test)
    rmsle.append(np.sqrt(mean_squared_log_error(test_pred,y_test)))
d={'Modelling Algo':model_names,'RMSLE':rmsle}   
d

{'Modelling Algo': ['RandomForestRegressor',
  'AdaBoostRegressor',
  'BaggingRegressor',
  'SVR',
  'KNeighborsRegressor'],
 'RMSLE': [0.30087401696552113,
  0.8465953687556789,
  0.29663300307672086,
  1.4160442277242877,
  1.2857079872932988]}

In [177]:
#for random forest regresion.
no_of_test=[200]
params_dict={'n_estimators':no_of_test,'n_jobs':[-1]}
clf_rf=GridSearchCV(estimator=BaggingRegressor(),param_grid=params_dict,scoring='neg_mean_squared_log_error')
clf_rf.fit(X_train,y_train)
pred=clf_rf.predict(X_test)
print((np.sqrt(mean_squared_log_error(pred,y_test))))

0.29014286329362293


In [178]:
clf_rf.best_params_

{'n_estimators': 200, 'n_jobs': -1}

In [183]:
df_predictions = pd.DataFrame(clf_rf.predict(test_set_final))
df_predictions.columns = ['countRents']
df_predictions.index = test_set_final.index
df_predictions.head()

countRents
datetime                       
2019-07-27 00:00:00     411.555
2019-07-27 01:00:00     292.880
2019-07-27 02:00:00     160.160
2019-07-27 03:00:00     127.570
2019-07-27 04:00:00      81.120

In [184]:
# write predictions to file

df_predictions.to_csv(os.path.join(file_path, 'predictions7.csv'))